In [1]:
import pandas as pd
import altair as alt
from altair import datum

alt.data_transformers.disable_max_rows()
alt.themes.enable('latimes')

ThemeRegistry.enable('latimes')

## Data loading and wrangling

In [2]:
eco = pd.read_csv('eco.csv')
my_cols= eco[eco.columns[2:16]].columns
eco.set_index(['Geography', 'Year', 'Industry'], inplace=True)

eco_gr = eco.pct_change().reset_index()
eco_gr.loc[eco_gr.Year == 1999, my_cols] = 0
eco_gr_cum = eco.pct_change().cumsum().reset_index()
eco_gr_cum.loc[eco_gr_cum.Year == 1999, my_cols] = 0
eco = eco.reset_index()

In [3]:
industry_gdp = pd.read_csv('industry.csv')
industry_gdp.set_index(['Geography', 'Year', 'Industry'], inplace=True)

industry_gdp_gr = industry_gdp.pct_change().reset_index()
industry_gdp_gr.loc[industry_gdp_gr.Year == 1999, 'Industry GDP'] = 0
industry_gdp_gr_cum = industry_gdp.pct_change().cumsum().reset_index()
industry_gdp_gr_cum.loc[industry_gdp_gr_cum.Year == 1999,  'Industry GDP'] = 0
industry_gdp = industry_gdp.reset_index()

In [4]:
labour = eco.groupby(['Geography', 'Year', 'Industry'])['Unemployment rate', 'Employed', 'Unemployed'].sum().reset_index()

<ipython-input-4-296c68f9ffac>:1: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  labour = eco.groupby(['Geography', 'Year', 'Industry'])['Unemployment rate', 'Employed', 'Unemployed'].sum().reset_index()


## Data Visualizations

### Filters

In [5]:
year=2019
geo='British Columbia'

In [10]:
gdp_vis

alt.VConcatChart(...)

### 1st. tab. Real GDP

In [8]:
real_gdp = alt.Chart(eco, title="Total GDP").mark_bar().transform_aggregate(
    groupby =['Geography', 'Year'], GDP='sum(Real GDP)').encode(
        x=alt.X('sum(GDP):Q', title='CA$ (MM)', axis=alt.Axis(titleFontSize=20, grid=False, ticks=False, labels=False)), 
        y=alt.Y('Geography:O', sort='-x', title=None, axis=alt.Axis(labelFontSize=20,ticks=False, grid=False)),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldEqualPredicate(field='Year', equal= year)).properties(
                height=200, width=400).mark_text(
                    dx=-175, color='darkblue', size=80).encode(
                        text=alt.Text('sum(GDP):Q', format=('$,')))

real_gdp_gr = alt.Chart(eco_gr, title="Growth rate").mark_bar().transform_aggregate(
    groupby =['Geography', 'Year'], GDP='sum(Real GDP)').encode(
        x=alt.X('sum(GDP):Q', title='Yearly %', axis=alt.Axis(titleFontSize=20, grid=False, ticks=False, labels=False)), 
        y=alt.Y('Geography:O', sort='-x', title=None, axis=alt.Axis(grid=False, ticks=False, labels=False)),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldEqualPredicate(field='Year', equal= year)).properties(
                height=200, width=400).mark_text(
                    dx=-175, color='darkblue', size=80).encode(
                        text=alt.Text('sum(GDP):Q', format=('.2%')))

real_gdp_evo = alt.Chart(eco, title="GDP evolution").mark_area(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue')).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('sum(Real GDP):Q', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, ticks=False, format=('$,f')), title=None),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('sum(Real GDP):Q', format=('$,'), title='GDP')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2000,year]))

real_gdp_rank = alt.Chart(eco, title="Contribution by province/territory").mark_bar().encode(
    x=alt.X('sum(Real GDP):Q', title='CA$ (MM)', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, format=('$,f'))), 
    y=alt.Y('Geography:O', sort='-x', axis=alt.Axis(labelFontSize=18), title=None),
    color=alt.condition((alt.datum.Geography == geo) | (alt.datum.Geography == 'Canada'), alt.value('darkblue'), alt.value('lightblue')),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('sum(Real GDP):Q', format=('$,'), title='GDP')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year))

real_gdp_gr_evo = alt.Chart(eco_gr, title="GDP growth rates").mark_bar(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue'), size=16).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('sum(Real GDP):Q', axis=alt.Axis(tickCount=3, grid=False, ticks=False, format=('%')), title=None),
        color=alt.condition((alt.datum.Year == year), alt.value('darkblue'), alt.value('lightblue')),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('sum(Real GDP):Q', format=('.2%'), title='Growth rate')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2000,year]))

real_gdp_gr_rank = alt.Chart(eco_gr, title="By province/territory").mark_bar().encode(
    x=alt.X('sum(Real GDP):Q', title=None, axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, format=('%'))), 
    y=alt.Y('Geography:O', sort='-x', axis=alt.Axis(labelFontSize=18), title=None),
    color=alt.condition((alt.datum.Geography == geo) | (alt.datum.Geography == 'Canada'), alt.value('darkblue'), alt.value('lightblue')),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('sum(Real GDP):Q', format=('.2%'), title='Growth rate')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year))

real_gdpca = alt.Chart(eco, title="GDP per Capita").mark_bar().transform_aggregate(
    groupby =['Geography', 'Year'], GDP='average(Real GDP per Capita)').encode(
        x=alt.X('sum(GDP):Q', title='CA$', axis=alt.Axis(titleFontSize=20, grid=False, ticks=False, labels=False)), 
        y=alt.Y('Geography:O', sort='-x', title=None, axis=alt.Axis(labelFontSize=20,ticks=False, grid=False)),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldEqualPredicate(field='Year', equal= year)).properties(
                height=200, width=400).mark_text(
                    dx=-175, color='darkblue', size=80).encode(
                        text=alt.Text('sum(GDP):Q', format=('$,.0f')))

real_gdpc_gr = alt.Chart(eco_gr, title="Growth rate").mark_bar().transform_aggregate(
    groupby =['Geography', 'Year'], GDP='average(Real GDP per Capita)').encode(
        x=alt.X('sum(GDP):Q', title='Yearly %', axis=alt.Axis(titleFontSize=20, grid=False, ticks=False, labels=False)), 
        y=alt.Y('Geography:O', sort='-x', title=None, axis=alt.Axis(grid=False, ticks=False, labels=False)),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldEqualPredicate(field='Year', equal= year)).properties(
                height=200, width=400).mark_text(
                    dx=-175, color='darkblue', size=80).encode(
                        text=alt.Text('sum(GDP):Q', format=('.2%')))

real_gdpc_evo = alt.Chart(eco, title="GDP per Capita evolution").mark_area(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue')).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('average(Real GDP per Capita):Q', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, ticks=False, format=('$,f')), title=None),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Real GDP per Capita):Q', format=('$,.0f'), title='GDP per Capita')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2000,year]))

real_gdpc_rank = alt.Chart(eco, title="By province/territory").mark_bar().encode(
    x=alt.X('average(Real GDP per Capita):Q', title='CA$', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, format=('$,f'))), 
    y=alt.Y('Geography:O', sort='-x', axis=alt.Axis(labelFontSize=18), title=None),
    color=alt.condition((alt.datum.Geography == geo) | (alt.datum.Geography == 'Canada'), alt.value('darkblue'), alt.value('lightblue')),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Real GDP per Capita):Q', format=('$,.0f'), title='GDP per Capita')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year))

real_gdpc_gr_evo = alt.Chart(eco_gr, title="GDP per Capita growth rates").mark_bar(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue'), size=16).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('average(Real GDP per Capita):Q', axis=alt.Axis(tickCount=3, grid=False, ticks=False, format=('%')), title=None),
        color=alt.condition((alt.datum.Year == year), alt.value('darkblue'), alt.value('lightblue')),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Real GDP per Capita):Q', format=('.2%'), title='Growth rate')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2000,year]))

real_gdpc_gr_rank = alt.Chart(eco_gr, title="By province/territory").mark_bar().encode(
    x=alt.X('average(Real GDP per Capita):Q', title=None, axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, format=('%'))), 
    y=alt.Y('Geography:O', sort='-x', axis=alt.Axis(labelFontSize=18), title=None),
    color=alt.condition((alt.datum.Geography == geo) | (alt.datum.Geography == 'Canada'), alt.value('darkblue'), alt.value('lightblue')),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Real GDP per Capita):Q', format=('.2%'), title='Growth rate')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year))

real_gdp_ind_rank = alt.Chart(industry_gdp, title="GDP contribution by industry").mark_bar().encode(
    y=alt.Y('sum(Industry GDP):Q', title='CA$ (MM)', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, format=('$,f'))), 
    x=alt.X('Industry:O', sort='-y', axis=alt.Axis(labelAngle=-90), title=None),
    color=alt.Color('sum(Industry GDP)', title='GDP', scale=alt.Scale(scheme='blues'), legend=alt.Legend(format=('$,f'))),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('Industry'), alt.Tooltip('sum(Industry GDP):Q', format=('$,.0f'), title='GDP')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year)).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).configure_view(strokeOpacity=0).configure_axis(domain=False, ticks=False).configure_title(fontSize=30)

real_gdp_ind_gr_rank = alt.Chart(industry_gdp_gr, title="GDP growth rate by industry").mark_bar().encode(
    y=alt.Y('sum(Industry GDP):Q', title=None, axis=alt.Axis(tickCount=3, grid=False, format=('%'))), 
    x=alt.X('Industry:O', sort='-y', title=None, axis=alt.Axis(labelLimit=90, labelAngle=-90)),
    color=alt.Color('sum(Industry GDP)', title='GDP growth rate', scale=alt.Scale(scheme='redblue'), legend=alt.Legend(format=('%'))),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('Industry'), alt.Tooltip('sum(Industry GDP):Q', format=('.2%'), title='Growth rate')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year)).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).configure_view(strokeOpacity=0).configure_axis(domain=False, ticks=False).configure_title(fontSize=30)

gdp_summary = (real_gdp | real_gdp_gr)
gdp_total = (real_gdp_evo | real_gdp_rank)
gdp_gr = (real_gdp_gr_evo | real_gdp_gr_rank)
gdp_vis = ((gdp_summary & gdp_total) & gdp_gr).configure_view(strokeOpacity=0).configure_axis(domain=False).configure_title(fontSize=30)

gdpc_summary =(real_gdpca | real_gdpc_gr)
gdpc_total = (real_gdpc_evo | real_gdpc_rank)
gdpc_gr = (real_gdpc_gr_evo | real_gdpc_gr_rank)
gdpc_vis = ((gdpc_summary & gdpc_total) & gdpc_gr).configure_view(strokeOpacity=0).configure_axis(domain=False).configure_title(fontSize=30)

In [7]:
gdp_vis

alt.VConcatChart(...)

In [981]:
gdpc_vis

alt.VConcatChart(...)

In [982]:
real_gdp_ind_rank

alt.Chart(...)

In [983]:
real_gdp_ind_gr_rank

alt.Chart(...)

### 2nd. tab. Nominal GDP

In [984]:
nominal_gdp = alt.Chart(eco, title="Total GDP").mark_bar().transform_aggregate(
    groupby =['Geography', 'Year'], GDP='sum(Nominal GDP)').encode(
        x=alt.X('sum(GDP):Q', title='CA$ (MM)', axis=alt.Axis(titleFontSize=20, grid=False, ticks=False, labels=False)), 
        y=alt.Y('Geography:O', sort='-x', title=None, axis=alt.Axis(labelFontSize=20,ticks=False, grid=False)),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldEqualPredicate(field='Year', equal= year)).properties(
                height=200, width=400).mark_text(
                    dx=-175, color='darkblue', size=80).encode(
                        text=alt.Text('sum(GDP):Q', format=('$,')))

nominal_gdp_gr = alt.Chart(eco_gr, title="Growth rate").mark_bar().transform_aggregate(
    groupby =['Geography', 'Year'], GDP='sum(Nominal GDP)').encode(
        x=alt.X('sum(GDP):Q', title='Yearly %', axis=alt.Axis(titleFontSize=20, grid=False, ticks=False, labels=False)), 
        y=alt.Y('Geography:O', sort='-x', title=None, axis=alt.Axis(grid=False, ticks=False, labels=False)),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldEqualPredicate(field='Year', equal= year)).properties(
                height=200, width=400).mark_text(
                    dx=-175, color='darkblue', size=80).encode(
                        text=alt.Text('sum(GDP):Q', format=('.2%')))

nominal_gdp_evo = alt.Chart(eco, title="GDP evolution").mark_area(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue')).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('sum(Nominal GDP):Q', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, ticks=False, format=('$,f')), title=None),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('sum(Nominal GDP):Q', format=('$,'), title='GDP')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2000,year]))

nominal_gdp_rank = alt.Chart(eco, title="Contribution by province/territory").mark_bar().encode(
    x=alt.X('sum(Nominal GDP):Q', title='CA$ (MM)', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, format=('$,f'))), 
    y=alt.Y('Geography:O', sort='-x', axis=alt.Axis(labelFontSize=18), title=None),
    color=alt.condition((alt.datum.Geography == geo) | (alt.datum.Geography == 'Canada'), alt.value('darkblue'), alt.value('lightblue')),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('sum(Nominal GDP):Q', format=('$,'), title='GDP')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year))

nominal_gdp_gr_evo = alt.Chart(eco_gr, title="GDP growth rates").mark_bar(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue'), size=16).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('sum(Nominal GDP):Q', axis=alt.Axis(tickCount=3, grid=False, ticks=False, format=('%')), title=None),
        color=alt.condition((alt.datum.Year == year), alt.value('darkblue'), alt.value('lightblue')),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('sum(Nominal GDP):Q', format=('.2%'), title='Growth rate')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2000,year]))

nominal_gdp_gr_rank = alt.Chart(eco_gr, title="By province/territory").mark_bar().encode(
    x=alt.X('sum(Nominal GDP):Q', title=None, axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, format=('%'))), 
    y=alt.Y('Geography:O', sort='-x', axis=alt.Axis(labelFontSize=18), title=None),
    color=alt.condition((alt.datum.Geography == geo) | (alt.datum.Geography == 'Canada'), alt.value('darkblue'), alt.value('lightblue')),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('sum(Nominal GDP):Q', format=('.2%'), title='Growth rate')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year))

nominal_gdpca = alt.Chart(eco, title="GDP per Capita").mark_bar().transform_aggregate(
    groupby =['Geography', 'Year'], GDP='average(Nominal GDP per Capita)').encode(
        x=alt.X('sum(GDP):Q', title='CA$', axis=alt.Axis(titleFontSize=20, grid=False, ticks=False, labels=False)), 
        y=alt.Y('Geography:O', sort='-x', title=None, axis=alt.Axis(labelFontSize=20,ticks=False, grid=False)),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldEqualPredicate(field='Year', equal= year)).properties(
                height=200, width=400).mark_text(
                    dx=-175, color='darkblue', size=80).encode(
                        text=alt.Text('sum(GDP):Q', format=('$,.0f')))

nominal_gdpc_gr = alt.Chart(eco_gr, title="Growth rate").mark_bar().transform_aggregate(
    groupby =['Geography', 'Year'], GDP='average(Nominal GDP per Capita)').encode(
        x=alt.X('sum(GDP):Q', title='Yearly %', axis=alt.Axis(titleFontSize=20, grid=False, ticks=False, labels=False)), 
        y=alt.Y('Geography:O', sort='-x', title=None, axis=alt.Axis(grid=False, ticks=False, labels=False)),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldEqualPredicate(field='Year', equal= year)).properties(
                height=200, width=400).mark_text(
                    dx=-175, color='darkblue', size=80).encode(
                        text=alt.Text('sum(GDP):Q', format=('.2%')))

nominal_gdpc_evo = alt.Chart(eco, title="GDP per Capita evolution").mark_area(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue')).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('average(Nominal GDP per Capita):Q', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, ticks=False, format=('$,f')), title=None),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Nominal GDP per Capita):Q', format=('$,.0f'), title='GDP per Capita')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2000,year]))

nominal_gdpc_rank = alt.Chart(eco, title="By province/territory").mark_bar().encode(
    x=alt.X('average(Nominal GDP per Capita):Q', title='CA$', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, format=('$,f'))), 
    y=alt.Y('Geography:O', sort='-x', axis=alt.Axis(labelFontSize=18), title=None),
    color=alt.condition((alt.datum.Geography == geo) | (alt.datum.Geography == 'Canada'), alt.value('darkblue'), alt.value('lightblue')),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Nominal GDP per Capita):Q', format=('$,.0f'), title='GDP per Capita')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year))

nominal_gdpc_gr_evo = alt.Chart(eco_gr, title="GDP per Capita growth rates").mark_bar(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue'), size=16).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('average(Nominal GDP per Capita):Q', axis=alt.Axis(tickCount=3, grid=False, ticks=False, format=('%')), title=None),
        color=alt.condition((alt.datum.Year == year), alt.value('darkblue'), alt.value('lightblue')),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Nominal GDP per Capita):Q', format=('.2%'), title='Growth rate')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2000,year]))

nominal_gdpc_gr_rank = alt.Chart(eco_gr, title="By province/territory").mark_bar().encode(
    x=alt.X('average(Nominal GDP per Capita):Q', title=None, axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, format=('%'))), 
    y=alt.Y('Geography:O', sort='-x', axis=alt.Axis(labelFontSize=18), title=None),
    color=alt.condition((alt.datum.Geography == geo) | (alt.datum.Geography == 'Canada'), alt.value('darkblue'), alt.value('lightblue')),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Nominal GDP per Capita):Q', format=('.2%'), title='Growth rate')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year))

ngdp_summary = (nominal_gdp | nominal_gdp_gr)
ngdp_total = (nominal_gdp_evo | nominal_gdp_rank)
ngdp_gr = (nominal_gdp_gr_evo | nominal_gdp_gr_rank)
ngdp_vis = ((ngdp_summary & ngdp_total) & ngdp_gr).configure_view(strokeOpacity=0).configure_axis(domain=False).configure_title(fontSize=30)

ngdpc_summary =(nominal_gdpca | nominal_gdpc_gr)
ngdpc_total = (nominal_gdpc_evo | nominal_gdpc_rank)
ngdpc_gr = (nominal_gdpc_gr_evo | nominal_gdpc_gr_rank)
ngdpc_vis = ((ngdpc_summary & ngdpc_total) & ngdpc_gr).configure_view(strokeOpacity=0).configure_axis(domain=False).configure_title(fontSize=30)

In [985]:
ngdp_vis

alt.VConcatChart(...)

In [986]:
ngdpc_vis

alt.VConcatChart(...)

### 3rd. tab. Labour Force

In [987]:
er_evo = alt.Chart(eco, title="Unemployment rate evolution").mark_area(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue')).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('average(Unemployment rate):Q', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, ticks=False, format=('%')), title=None),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Unemployment rate):Q', format=('.2%'), title='Unemployment rate')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2000,year])).properties(height=430)

er_rank = alt.Chart(eco, title="Unemployment rate by province/territory").mark_bar().encode(
    x=alt.X('average(Unemployment rate):Q', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, ticks=False, format=('%')), title=None), 
    y=alt.Y('Geography:O', sort='-x', axis=alt.Axis(labelFontSize=18), title=None),
    color=alt.condition((alt.datum.Geography == geo) | (alt.datum.Geography == 'Canada'), alt.value('darkblue'), alt.value('lightblue')),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Unemployment rate):Q', format=('.2%'), title='Unemployment rate')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year))

er_ind_rank= alt.Chart(labour, title="Unemployment rate by industry").mark_bar().encode(
    x=alt.X('Unemployment rate:Q', axis=alt.Axis(tickCount=3, grid=False, ticks=False, format=('%')), title=None), 
    y=alt.Y('Industry:O', sort='-x', axis=alt.Axis(labelFontSize=18), title=None),
    color=alt.value('lightblue'),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('Industry'), alt.Tooltip('Unemployment rate:Q', format=('.2%'), title='Unemployment rate')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year)).transform_filter(
        alt.FieldEqualPredicate(field='Geography', equal= geo))

all_ear_evo = alt.Chart(eco, title="All industries").mark_area(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue')).encode(
        x=alt.X('Year', title='CA$', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('average(All industries):Q', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, ticks=False, format=('$,f')), title=None),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(All industries):Q', format=('$,'), title='Earnings')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2002,year]))

all_ear_gr_evo = alt.Chart(eco_gr, title="Growth rates").mark_bar(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue'), size=16).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('average(All industries):Q', axis=alt.Axis(tickCount=3, grid=False, ticks=False, format=('%')), title=None),
        color=alt.condition((alt.datum.Year == year), alt.value('darkblue'), alt.value('lightblue')),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(All industries):Q', format=('.2%'), title='Growth rate')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2002,year]))

goods_ear_evo = alt.Chart(eco, title="Goods-producing sector").mark_area(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue')).encode(
        x=alt.X('Year', title='CA$', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('average(Goods-producing sector):Q', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, ticks=False, format=('$,f')), title=None),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Goods-producing sector):Q', format=('$,'), title='Earnings')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2002,year]))

goos_ear_gr_evo = alt.Chart(eco_gr, title="Growth rates").mark_bar(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue'), size=16).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('average(Goods-producing sector):Q', axis=alt.Axis(tickCount=3, grid=False, ticks=False, format=('%')), title=None),
        color=alt.condition((alt.datum.Year == year), alt.value('darkblue'), alt.value('lightblue')),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Goods-producing sector):Q', format=('.2%'), title='Growth rate')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2002,year]))

serv_ear_evo = alt.Chart(eco, title="Service-producing").mark_area(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue')).encode(
        x=alt.X('Year', title='CA$', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('average(Service-producing sector):Q', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, ticks=False, format=('$,f')), title=None),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Service-producing sector):Q', format=('$,'), title='Earnings')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2002,year]))

serv_ear_gr_evo = alt.Chart(eco_gr, title="Growth rates").mark_bar(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue'), size=16).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('average(Service-producing sector):Q', axis=alt.Axis(tickCount=3, grid=False, ticks=False, format=('%')), title=None),
        color=alt.condition((alt.datum.Year == year), alt.value('darkblue'), alt.value('lightblue')),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Service-producing sector):Q', format=('.2%'), title='Growth rate')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2002,year]))

ear_rank = alt.Chart(eco, title="Average weekly earnings by province/territory").mark_bar().encode(
    x=alt.X('average(All industries):Q', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, ticks=False, format=('$,f')), title=None), 
    y=alt.Y('Geography:O', sort='-x', axis=alt.Axis(labelFontSize=18), title=None),
    color=alt.condition((alt.datum.Geography == geo) | (alt.datum.Geography == 'Canada'), alt.value('darkblue'), alt.value('lightblue')),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(All industries):Q', format=('$,'), title='Earnings')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year)).configure_view(strokeOpacity=0).configure_axis(domain=False).configure_title(fontSize=30)

employment_vis = (er_evo | (er_rank & er_ind_rank)).configure_view(strokeOpacity=0).configure_axis(domain=False).configure_title(fontSize=30)

all_ear = (all_ear_evo | all_ear_gr_evo)
goods_ear = (goods_ear_evo | goos_ear_gr_evo)
serv_ear = (serv_ear_evo | serv_ear_gr_evo)
earnings_vis = ((all_ear & serv_ear) & goods_ear).configure_view(strokeOpacity=0).configure_axis(domain=False).configure_title(fontSize=30)

In [988]:
employment_vis

alt.HConcatChart(...)

In [989]:
earnings_vis

alt.VConcatChart(...)

In [990]:
ear_rank

alt.Chart(...)

### 4th. tab. Inflation

In [991]:
all_cpi_evo = alt.Chart(eco, title="CPI all-items evolution").mark_area(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue')).encode(
        x=alt.X('Year', title='2002=100', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('average(All-items):Q', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, ticks=False, format=(',.0f')), title=None),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(All-items):Q', format=('.0f'), title='CPI')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2000,year]))

all_cpi_gr = alt.Chart(eco_gr, title="Growth rates").mark_bar(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue'), size=16).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('sum(All-items):Q', axis=alt.Axis(tickCount=3, grid=False, ticks=False, format=('%')), title=None),
        color=alt.condition((alt.datum.Year == year), alt.value('darkblue'), alt.value('lightblue')),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('sum(All-items):Q', format=('.2%'), title='Growth rate')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2000,year]))

gasoline_cpi_evo = alt.Chart(eco, title="CPI gasoline evolution").mark_area(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue')).encode(
        x=alt.X('Year', title='2002=100', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('average(Gasoline):Q', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, ticks=False, format=(',.0f')), title=None),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(Gasoline):Q', title='CPI')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2000,year]))

gasoline_cpi_gr = alt.Chart(eco_gr, title="Growth rates").mark_bar(
    point=alt.OverlayMarkDef(filled=False, fill='darkblue'), size=16).encode(
        x=alt.X('Year', title='Year', axis=alt.Axis(tickCount=5, titleFontSize=20, grid=False, ticks=False, format='Y')),
        y=alt.Y('sum(Gasoline):Q', axis=alt.Axis(tickCount=3, grid=False, ticks=False, format=('%')), title=None),
        color=alt.condition((alt.datum.Year == year), alt.value('darkblue'), alt.value('lightblue')),
        tooltip = [alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('sum(Gasoline):Q', format=('.2%'), title='Growth rate')]).transform_filter(
            alt.FieldEqualPredicate(field='Geography', equal= geo)).transform_filter(
            alt.FieldRangePredicate('Year',[2000,year]))

cpi_rank = alt.Chart(eco, title="CPI all-items by province/territory").mark_bar().encode(
    x=alt.X('average(All-items):Q', title='2002=100', axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, format=(',.0f'))), 
    y=alt.Y('Geography:O', sort='-x', axis=alt.Axis(labelFontSize=18), title=None),
    color=alt.condition((alt.datum.Geography == geo) | (alt.datum.Geography == 'Canada'), alt.value('darkblue'), alt.value('lightblue')),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(All-items):Q', title='CPI')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year))

cpi_gr_rank = alt.Chart(eco_gr, title="Growth rate by province/territory").mark_bar().encode(
    x=alt.X('average(All-items):Q', title=None, axis=alt.Axis(tickCount=3, titleFontSize=20, grid=False, format=('%'))), 
    y=alt.Y('Geography:O', sort='-x', axis=alt.Axis(labelFontSize=18), title=None),
    color=alt.condition((alt.datum.Geography == geo) | (alt.datum.Geography == 'Canada'), alt.value('darkblue'), alt.value('lightblue')),
    tooltip=[alt.Tooltip('Geography', title='Province/territory'), alt.Tooltip('Year'), alt.Tooltip('average(All-items):Q', format=('.2%'), title='CPI')]).transform_filter(
        alt.FieldEqualPredicate(field='Year', equal= year))

all_cpi = (all_cpi_evo | all_cpi_gr)
gasoline_cpi = (gasoline_cpi_evo | gasoline_cpi_gr)
rank_cpi = (cpi_rank | cpi_gr_rank)
cpi_vis = ((all_cpi & gasoline_cpi) & rank_cpi).configure_view(strokeOpacity=0).configure_axis(domain=False).configure_title(fontSize=30)

In [992]:
cpi_vis

alt.VConcatChart(...)